In [7]:
# NYC Airbnb 이중모델 기반 가성비 숙소 분석 (회귀 + 분류)
import pandas as pd
import folium
from folium.plugins import MarkerCluster
from sklearn.ensemble import RandomForestRegressor, RandomForestClassifier
from sklearn.model_selection import train_test_split

# ----------------------------
# Step 1: 데이터 불러오기
# ----------------------------
df = pd.read_csv("clean_NYC_v1.csv")

# ----------------------------
# Step 2: 회귀 및 분류 모델 학습
# ----------------------------
features = ['latitude', 'longitude', 'minimum_nights'] + \
    [col for col in df.columns if 'neighbourhood_group_' in col or 'room_type_' in col]

# 회귀 설정
X_reg = df[features]
y_reg = df['price']

# 분류용 price 구간 생성 (target)
df['actual_class'] = pd.qcut(df['price'], q=3, labels=['Low', 'Medium', 'High'])
y_cls = df['actual_class']
X_cls = X_reg.copy()

# 데이터 분할
X_reg_train, X_reg_test, y_reg_train, y_reg_test = train_test_split(X_reg, y_reg, test_size=0.2, random_state=42)
X_cls_train, X_cls_test, y_cls_train, y_cls_test = train_test_split(X_cls, y_cls, test_size=0.2, random_state=42)

# 모델 학습
reg_model = RandomForestRegressor(random_state=42)
reg_model.fit(X_reg_train, y_reg_train)

cls_model = RandomForestClassifier(random_state=42)
cls_model.fit(X_cls_train, y_cls_train)

# 예측
df['predicted_price'] = reg_model.predict(X_reg)
df['predicted_class'] = cls_model.predict(X_cls)

# ----------------------------
# Step 3: 가성비 숙소 판단 기준
# ----------------------------
# 조건 1: 실제 가격이 회귀 예측 가격보다 낮음
price_condition = df['price'] < df['predicted_price']

# 조건 2: 예측 등급 vs 실제 등급 차이
def classification_gaseongbi(row):
    if row['predicted_class'] == 'High' and row['actual_class'] in ['Medium', 'Low']:
        return True
    elif row['predicted_class'] == 'Medium' and row['actual_class'] == 'Low':
        return True
    return False

classification_condition = df.apply(classification_gaseongbi, axis=1)

# 최종 가성비 조건
df['gaseongbi_flag'] = price_condition & classification_condition

# ----------------------------
# Step 4: 특정 지역 시각화
# ----------------------------
target_area = 'Harlem'  # 원하는 지역 변경 가능
subset_df = df[df['neighbourhood'] == target_area].copy()

m = folium.Map(location=[subset_df['latitude'].mean(), subset_df['longitude'].mean()], zoom_start=14)
cluster = MarkerCluster().add_to(m)

for _, row in subset_df.iterrows():
    popup_text = (
        f"<b>Neighbourhood:</b> {row['neighbourhood']}<br>"
        f"<b>Actual Price:</b> ${row['price']}<br>"
        f"<b>Predicted Price:</b> ${row['predicted_price']:.2f}<br>"
        f"<b>Actual Class:</b> {row['actual_class']}<br>"
        f"<b>Predicted Class:</b> {row['predicted_class']}<br>"
        f"<b>Gaseongbi:</b> {'✅ YES' if row['gaseongbi_flag'] else '❌ NO'}"
    )

    folium.Marker(
        location=[row['latitude'], row['longitude']],
        popup=popup_text,
        icon=folium.Icon(color="green" if row['gaseongbi_flag'] else "gray")
    ).add_to(cluster)

# ----------------------------
# Step 5: 결과 요약
# ----------------------------
print(f"📍 지역: {target_area}")
print(f"총 숙소 수: {len(subset_df)}")
print(f"가성비 숙소 수: {subset_df['gaseongbi_flag'].sum()}")

# 지도 출력
m


📍 지역: Harlem
총 숙소 수: 2639
가성비 숙소 수: 86
